# Decision Tree


For this problem, you will be implementing a Decision Tree classifier that works on discrete (categorical) features. Although a relatively simple learning algorithm, the Decision Tree is often used as a fundamental building block for more powerful (and popular) models such as Random Forest and Gradient Boosted ensembles. 

You should base your solution on the [ID3](https://en.wikipedia.org/wiki/ID3_algorithmhttps://en.wikipedia.org/wiki/ID3_algorithm) algorithm. This is a basic tree-learning algorithm that greedly grows a tree based on _information gain_ (reduction in entropy). Please refer to Chapter 3 of _Machine Learning_ by Tom M. Mitchell for more details. 


We have provided some skeleton code for the classifier, along with a couple of utility functions in the [decision_tree.py](./decision_tree.py) module. Please fill out the functions marked with `TODO` and feel free to add extra constructor arguments as you see fit (just make sure the default constructor solves the first dataset).


In [282]:
%load_ext autoreload

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


We begin by loading necessary packages. Below follows a short description of the imported modules:

- `numpy` is the defacto python package for numerical calculation. Most other numerical libraries (including pandas) is based on numpy.
- `pandas` is a widely used package for manipulating (mostly) tabular data
- `decision_tree` refers to the module in this folder that should be further implemented by you

Note: The `%autoreload` statement is an [IPython magic command](https://ipython.readthedocs.io/en/stable/interactive/magics.html) that automatically reloads the newest version of all imported modules within the cell. This means that you can edit the `decision_tree.py` file and just rerun this cell to get the updated version.

In [283]:
%autoreload

import numpy as np 
import pandas as pd
import decision_tree as dt  # <-- Your implementation

## [1] First Dataset

The first dataset is a toy problem lifted from Table 3.2 in the Machine Learning textbook. The objective is to predict whether a given day is suitable for playing tennis based on several weather conditions. 

### [1.1] Load Data

We begin by loading data from the .csv file located in the same folder as this notebook.

In [284]:
data_1 = pd.read_csv('data_1.csv')
data_1

Outlook Temperature Humidity    Wind Play Tennis
0      Sunny         Hot     High    Weak          No
1      Sunny         Hot     High  Strong          No
2   Overcast         Hot     High    Weak         Yes
3       Rain        Mild     High    Weak         Yes
4       Rain        Cool   Normal    Weak         Yes
5       Rain        Cool   Normal  Strong          No
6   Overcast        Cool   Normal  Strong         Yes
7      Sunny        Mild     High    Weak          No
8      Sunny        Cool   Normal    Weak         Yes
9       Rain        Mild   Normal    Weak         Yes
10     Sunny        Mild   Normal  Strong         Yes
11  Overcast        Mild     High  Strong         Yes
12  Overcast         Hot   Normal    Weak         Yes
13      Rain        Mild     High  Strong          No

### [1.2] Fit and Evaluate Model

Next we fit and evaluate a Decision Tree over the dataset. We first partition the data into the dependent (`y` = Play Tennis) and independent (`X` = everything else) variables. We then initialize a Decision Tree learner and fit it to all the data. Finally, we evaluate the model over the same data by calculating its accuracy, i.e. the fraction of correctly classified samples.

Note that `.fit` and `.predict` will crash until you implement these two methods in [decision_tree.py](./decision_tree.py).

Assuming that you've correctly implemented the ID3 algorithm as described in the course textbook, you should expect the model to perfectly fit the training data. That is, you should get a classification accuracy of 100%.

In [285]:
X = data_1.drop(columns=['Play Tennis'])
y = data_1['Play Tennis']

# Create and fit a Decrision Tree classifier
model_1 = dt.DecisionTree()  # <-- Should work with default constructor
model_1.fit(X, y)

data_1 = pd.read_csv('data_1.csv')
X = data_1.drop(columns=['Play Tennis'])
y = data_1['Play Tennis']

print(model_1.predict(X))

# Verify that it perfectly fits the training set
print(f'Accuracy: {dt.accuracy(y_true=y, y_pred=model_1.predict(X)) * 100 :.1f}%')

[0, 1, 7, 8, 10]
[0, 1, 7]
[8, 10]
[2, 6, 11, 12]
[3, 4, 5, 9, 13]
[3, 4, 9]
[5, 13]
[[[('Outlook', 'Sunny'), ('Humidity', 'High')], 'No'], [[('Outlook', 'Sunny'), ('Humidity', 'Normal')], 'Yes'], [[('Outlook', 'Overcast')], 'Yes'], [[('Outlook', 'Rain'), ('Wind', 'Weak')], 'Yes'], [[('Outlook', 'Rain'), ('Wind', 'Strong')], 'No']]
[('Outlook', 'Sunny'), ('Humidity', 'High')]
[('Outlook', 'Sunny'), ('Humidity', 'Normal')]
[('Outlook', 'Overcast')]
[('Outlook', 'Rain'), ('Wind', 'Weak')]
[('Outlook', 'Rain'), ('Wind', 'Strong')]
0      No
1      No
2     Yes
3     Yes
4     Yes
5      No
6     Yes
7      No
8     Yes
9     Yes
10    Yes
11    Yes
12    Yes
13     No
dtype: object
[[[('Outlook', 'Sunny'), ('Humidity', 'High')], 'No'], [[('Outlook', 'Sunny'), ('Humidity', 'Normal')], 'Yes'], [[('Outlook', 'Overcast')], 'Yes'], [[('Outlook', 'Rain'), ('Wind', 'Weak')], 'Yes'], [[('Outlook', 'Rain'), ('Wind', 'Strong')], 'No']]
[('Outlook', 'Sunny'), ('Humidity', 'High')]
[('Outlook', 'Sunn

### [1.3] Inspect Classification Rules

A big advantage of Decision Trees is that they are relatively transparent learners. By this we mean that it is easy for an outside observer to analyse and understand how the model makes its decisions. The problem of being able to reason about how a machine learning model reasons is known as _Explainable AI_ and is often a desirable property of machine learning systems.

Every time a Decision Tree is evaluated, the datapoint is compared against a set of nodes starting at the root of the tree and (typically) ending at one of the leaf nodes. An equivalent way to view this reasoning is as an implication rule ($A \rightarrow B$) where the antecedent ($A$) is a conjunction of of attribute values and the consequent ($B$) is the predicted label. For instance, if a path down the tree first checks if Outlook=Rain, then checks if Wind=Strong, and then predicts Play Tennis=No, this line of reasoning can be represented as:

- If $Outlook=Rain \cap Wind=Strong \rightarrow$ then predict $Play Tennis = No$

We will leverage this property to export the decision tree you just created as a set of rules. For the subsequent cell to work, you must also have implemented the `.get_rules()` method in the provided boilerplate code.

In [286]:
for rules, label in model_1.get_rules():
    conjunction = ' ∩ '.join(f'{attr}={value}' for attr, value in rules)
    print(f'{"✅" if label == "Yes" else "❌"} {conjunction} => {label}')

❌ Outlook=Sunny ∩ Humidity=High => No
✅ Outlook=Sunny ∩ Humidity=Normal => Yes
✅ Outlook=Overcast => Yes
✅ Outlook=Rain ∩ Wind=Weak => Yes
❌ Outlook=Rain ∩ Wind=Strong => No


## [2] Second Dataset

The second dataset involves predicting whether an investment opportunity will result in a successful `Outcome` or not. To make this prediction, you are given a dataset of 200 historical$^1$ business ventures and their outcome, along with the following observed features:

- Whether the business oportunity is in a lucurative market or not 
- Whether the presented business idea has a competitive advantage
- Whether the second opinion from another investor is positive or not 
- The founder's previous experience with startups
- The founder's Birth Month.

---
[1] Disclaimer: The dataset is not based on real-world business ventures. It is synthetic and generated by us. Also, it should not be considered financial advice.

### [2.1] Load Data

This dataset can also be found in a .csv file in the same folder as this notebook.

In [287]:
data_2 = pd.read_csv('data_2.csv')
data_2

Birth Month Founder Experience Second Opinion Competitive Advantage  \
0           Jun           moderate       negative                   yes   
1           Jun               high       positive                   yes   
2           Oct                low       negative                    no   
3           Jun                low       negative                    no   
4           Jan                low       positive                   yes   
..          ...                ...            ...                   ...   
195         Dec           moderate       positive                    no   
196         Jan                low       negative                    no   
197         Jun           moderate       negative                    no   
198         Aug           moderate       negative                    no   
199         Dec           moderate       negative                   yes   

    Lucurative Market  Outcome  Split  
0                  no  success  train  
1                  no  failure  train  
2                  no  failure  train  
3                  no  failure  train  
4                 yes  success  train  
..                ...      ...    ...  
195               yes  failure   test  
196                no  failure   test  
197                no  failure   test  
198                no  failure   test  
199                no  success   test  

[200 rows x 7 columns]

### [2.2] Split Data

We've also taken the liberty to pre-split the dataset into three different sets:

- `train` contains 50 samples that you should use to generate the tree
- `valid` contains 50 samples that you can use to evaluate different preprocessing methods and variations to the tree-learning algorithm.
- `test` contains 100 samples and should only be used to evaluate the final model once you're done experimenting.

In [288]:
data_2_train = data_2.query('Split == "train"')
data_2_valid = data_2.query('Split == "valid"')
data_2_test = data_2.query('Split == "test"')
X_train, y_train = data_2_train.drop(columns=['Outcome', 'Split']), data_2_train.Outcome
X_valid, y_valid = data_2_valid.drop(columns=['Outcome', 'Split']), data_2_valid.Outcome
X_test, y_test = data_2_test.drop(columns=['Outcome', 'Split']), data_2_test.Outcome
data_2.Split.value_counts()

Split
test     100
train     50
valid     50
Name: count, dtype: int64

### [2.3] Fit and Evaluate Model

You may notice that the basic ID3 algorithm you developed for the first dataset does not generalize well when applied straight to this problem. Feel free to add extra functionality to it and/or the data preprocessing pipeline that might improve performance on the validation (and ultimately test set). As a debugging reference; it is highly possible to obtain accuracies over the validation and test set ranging from mid ~80% to low ~90%.

In [289]:
# Fit model (TO TRAIN SET ONLY)
model_2 = dt.DecisionTree(max_depth=3, n_trees=2, min_samples_split = 4, bagging=True, bag_frac=0.6)  # <-- Feel free to add hyperparameters 
model_2.fit(X_train, y_train)

print(f'Train: {dt.accuracy(y_train, model_2.predict(X_train)) * 100 :.1f}%')
print(len(model_2.predict(X_valid)))

print(f'Valid: {dt.accuracy(y_valid, model_2.predict(X_valid)) * 100 :.1f}%')

print(model_2.predict(X_test))
print(f'Valid: {dt.accuracy(y_test, model_2.predict(X_test)) * 100 :.1f}%')

[28]
[31, 10]
[12]
[33, 29]
[44, 9, 11]
[6, 24, 2]
[22, 1, 30, 8, 3, 0, 17]
[22, 30, 3]
[1, 8, 17]
[0]
[32, 40, 36, 21]
[20, 49, 16, 26]
[20]
[49, 16, 26]
[19]
[42, 7]
[9, 46, 18, 11, 48]
[9, 46, 18, 48]
[11]
[7, 13]
[35, 3, 1, 30, 8, 0, 47, 38, 22]
[35, 3, 30, 22]
[1, 8]
[0, 47, 38]
[2, 23, 24, 6, 43]
[5, 28]
[16, 20, 25]
[45, 40, 39]
[37]
0
[[[('Birth Month', 'Jan')], 'failure'], [[('Birth Month', 'Nov')], 'failure'], [[('Birth Month', 'May')], 'failure'], [[('Birth Month', 'Sep')], 'failure'], [[('Birth Month', 'Apr')], 'failure'], [[('Birth Month', 'Oct')], 'failure'], [[('Birth Month', 'Jun'), ('Founder Experience', 'low')], 'failure'], [[('Birth Month', 'Jun'), ('Founder Experience', 'high')], 'failure'], [[('Birth Month', 'Jun'), ('Founder Experience', 'moderate')], 'success'], [[('Birth Month', 'Feb')], 'failure'], [[('Birth Month', 'Mar'), ('Second Opinion', 'positive')], 'success'], [[('Birth Month', 'Mar'), ('Second Opinion', 'negative')], 'failure'], [[('Birth Month', 'Jul'

In [290]:
# Fit model (TO TRAIN SET ONLY)
model_2 = dt.DecisionTree(max_depth = 1, bagging=True, bag_frac=0.6, n_trees=10)  # <-- Feel free to add hyperparameters 
model_2.fit(X_train, y_train)


print(f'Train: {dt.accuracy(y_train, model_2.predict(X_train)) * 100 :.1f}%')
print(f'Valid: {dt.accuracy(y_valid, model_2.predict(X_valid)) * 100 :.1f}%')
print(f'Valid: {dt.accuracy(y_test, model_2.predict(X_test)) * 100 :.1f}%')

test_n_trees = np.arange(2, 12, 1)
test_bag_frac = np.arange(0.1, 0.9, 0.05)
test_max_depths = np.arange(1, 6)

def grid_search(X_train: pd.DataFrame, y_train: pd.Series, X_valid, y_valid, test_n_trees, test_bag_frac, max_depth: int):
    runs = 10
    results = np.zeros((len(test_n_trees), len(test_bag_frac)))
    
    for i, n_trees in enumerate(test_n_trees):
        for j, bag_frac in enumerate(test_bag_frac):
            for _ in range(runs):
                model_2 = dt.DecisionTree(max_depth = max_depth, bagging=True, bag_frac=bag_frac, n_trees=n_trees)  # <-- Feel free to add hyperparameters 
                model_2.fit(X_train, y_train)

                acc = dt.accuracy(y_valid, model_2.predict(X_valid)) * 100
                results[i, j] += acc /runs

    return results


def heatmap(results, test_bag_frac, test_n_trees):
    plt.figure(figsize=(8, 8))
    plt.imshow(results, cmap='viridis', interpolation='nearest')
    plt.colorbar(label='Accuracy')
    plt.xlabel('Bagging Fraction')
    plt.ylabel('Number of Trees')

    plt.xticks(np.arange(len(test_bag_frac)), test_bag_frac.round(2), rotation=45)
    plt.yticks(np.arange(len(test_n_trees)), test_n_trees)

    plt.title('Grid Search Results')

test_max_depth = 3

results = grid_search(X_train, y_train, X_valid, y_valid, test_n_trees, test_bag_frac, test_max_depth)
heatmap(results, test_bag_frac, test_n_trees)

[44, 46]
[30, 1, 17, 3, 35, 22]
[31, 41]
[14, 28, 4]
[16, 20, 25]
[40, 36, 32, 45]
[43, 24, 6, 2, 34]
[13, 7]
[27]
[33]
[37]
[11, 18, 44, 9, 48]
[6, 2]
[42, 13]
[8, 47, 17, 3, 38]
[4, 5, 14]
[20, 25]
[12, 37]
[33, 29]
[45, 21, 32, 40]
[41, 31]
[19]
[31]
[38, 17, 3, 30, 0, 22, 47]
[24, 6, 23, 34]
[18, 48, 9]
[37, 15]
[29]
[21, 40, 32, 45]
[14, 4]
[49, 16, 25, 26]
[7, 42]
[19]
[21, 40, 39, 45, 32, 36]
[38, 47, 30, 0]
[23, 34, 2, 43]
[9, 46, 18, 48, 11]
[16, 26, 49, 20]
[10]
[27]
[33]
[12, 37]
[5]
[28, 14, 5]
[35, 17, 1, 3, 47, 30]
[7, 42, 13]
[18, 9, 11]
[49, 26, 25, 16]
[27]
[41, 31, 10]
[24, 23, 6, 2]
[19]
[40]
[29]
[35, 47, 1, 17, 38, 3]
[29, 33]
[28, 4]
[40, 32, 36, 45, 21]
[20, 25]
[18, 11, 48]
[24, 2, 6]
[15, 37]
[31, 10, 41]
[42]
[27]
[47, 17, 35, 1, 30, 38, 22, 3]
[26, 25, 16, 49]
[23, 43]
[45, 36, 39, 21]
[44, 18, 9]
[42, 13]
[41, 10]
[15]
[5, 4]
[19]
[33]
[44, 48, 11, 9, 46]
[45, 40, 21, 39]
[0, 1, 8, 35, 3, 38]
[31, 10, 41]
[29, 33]
[25, 16, 20]
[28]
[27]
[43, 34, 2, 6]
[37]
[

In [ ]:



def total_entropy(y: pd.Series, X_col: pd.Series):
    

    total_ent = 0
    n = len(y)
    grouped  = X_col.groupby(X_col)
    for name, group in grouped:

        weight = len(group.index)/n
        counts = y[group.index].value_counts().values

        ent = entropy(counts)
        
        total_ent = total_ent + weight*ent
        
    return total_ent


def entropy(counts: np.array):
        """
        Computes the entropy of a partitioning

        Args:
            counts (array<k>): a lenth k int array >= 0. For instance,
                an array [3, 4, 1] implies that you have a total of 8
                datapoints where 3 are in the first group, 4 in the second,
                and 1 one in the last. This will result in entropy > 0.
                In contrast, a perfect partitioning like [8, 0, 0] will
                result in a (minimal) entropy of 0.0
                
        Returns:
            A positive float scalar corresponding to the (log2) entropy
            of the partitioning.

        """
        assert (counts >= 0).all()
        probs = counts / counts.sum()
        probs = probs[probs > 0]  # Avoid log(0)
        return - np.sum(probs * np.log2(probs))

data_1 = pd.read_csv('data_1.csv')


X = data_1.drop(columns=['Play Tennis'])
y = data_1['Play Tennis']
features = X.columns.values
entrops = []

for feat in features:
    print(feat)
    print(total_entropy(y, X[feat]))
    entrops.append((feat, total_entropy(y, X[feat])))

print(entrops)

Outlook
Overcast
-0.0

Rain
0.9709505944546686

Sunny
0.9709505944546686

Total ent
0.6935361388961918
Overcast
-0.0

Rain
0.9709505944546686

Sunny
0.9709505944546686

Total ent
Temperature
Cool
0.8112781244591328

Hot
1.0

Mild
0.9182958340544896

Total ent
0.9110633930116763
Cool
0.8112781244591328

Hot
1.0

Mild
0.9182958340544896

Total ent
Humidity
High
0.9852281360342515

Normal
0.5916727785823275

Total ent
0.7884504573082896
High
0.9852281360342515

Normal
0.5916727785823275

Total ent
Wind
Strong
1.0

Weak
0.8112781244591328

Total ent
0.8921589282623617
Strong
1.0

Weak
0.8112781244591328

Total ent
[('Outlook', 0.6935361388961918), ('Temperature', 0.9110633930116763), ('Humidity', 0.7884504573082896), ('Wind', 0.8921589282623617)]


## [3] Further steps (optional)

If you're done with the assignment but want to some more challenges; consider the following:

- Make a Decision Tree learner that can handle numerical attributes
- Make a Decision Tree learner that can handle numerical targets (regresion tree)
- Try implementing [Random Forest](https://en.wikipedia.org/wiki/Random_forest) on top of your Decision Tree algorithm

If you need more data for experimenting, UC Irvine hosts a [large repository](https://archive.ics.uci.edu/ml/datasets.php) of machine learning datasets.
